In [2]:
%cd VideoMAEv2

/home/exouser/VideoMAEv2


In [3]:
import torch
print(torch.cuda.is_available())
print(torch.cuda.get_device_name(0))

True
GRID A100X-40C


In [4]:
import os

current_dir = os.getcwd()
print("Current Directory:", current_dir)

Current Directory: /home/exouser/VideoMAEv2


In [4]:
import torch
from models.modeling_pretrain import pretrain_videomae_large_patch16_224

# If the function requires specific arguments, provide them here
model = pretrain_videomae_large_patch16_224()

# Count the number of parameters
total_params = sum(p.numel() for p in model.parameters())
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)

print(f"Total parameters: {total_params}")
print(f"Trainable parameters: {trainable_params}")

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


Total parameters: 330389504
Trainable parameters: 330389504


In [6]:
# Define paths and any environment variables first
OUTPUT_DIR = 'work_dir/pretrain_videomae_large_patch16_224'
DATA_PATH = 'train.csv'

import os
# --num_workers 24 
# Set environment variable
os.environ["OMP_NUM_THREADS"] = "1"

# Execute the python script with necessary parameters
!python -u run_mae_pretraining.py \
        --data_path {DATA_PATH} \
        --mask_type tube \
        --mask_ratio 0.9 \
        --decoder_mask_type run_cell \
        --decoder_mask_ratio 0.5 \
        --model pretrain_videomae_large_patch16_224 \
        --decoder_depth 4 \
        --batch_size 16 \
        --num_frames 16 \
        --sampling_rate 4 \
        --num_sample 2 \
        --num_workers 28 \
        --opt adamw \
        --lr 6e-4 \
        --clip_grad 0.02 \
        --opt_betas 0.9 0.95 \
        --warmup_epochs 30 \
        --save_ckpt_freq 20 \
        --epochs 300 \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR}

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(auto_resume=True, batch_size=16, clip_grad=0.02, color_jitter=0.0, data_path='train.csv', data_root='', decoder_depth=4, decoder_mask_ratio=0.5, decoder_mask_type='run_cell', device='cuda', dist_on_itp=False, dist_url='env://', distributed=False, drop_path=0.0, epochs=300, finetune='', fname_tmpl='img_{:05}.jpg', imagenet_default_mean_and_std=True, input_size=224, local_rank=-1, log_dir='work_dir/pretrain_videomae_large_patch16_224', lr=0.0006, mask_ratio=0.9, mask_type='tube', min_lr=1e-05, model='pretrain_videomae_large_patch16_224', momentum=0.9, normlize_target=True, num_frames=16, num_sample=2, num_workers=28, opt='adamw', opt_betas=[0.9, 0.95], opt_eps=1e-08, output_dir='wor

In [8]:
import json

# Path to the log file
log_file_path = "work_dir/pretrain_videomae_large_patch16_224/log.txt"

# Initialize minimum loss to a large value and line number to None
min_loss = float('inf')
min_loss_line_num = None

# Open the log file and process each line
with open(log_file_path, 'r') as log_file:
    for i, line in enumerate(log_file):
        # Check if the line number matches the given condition
        if i % 20 == 19 and i <= 300:
            data = json.loads(line)
            if 'train_loss' in data and data['train_loss'] < min_loss:
                min_loss = data['train_loss']
                min_loss_line_num = i

print(f"The smallest loss is {min_loss} at line number {min_loss_line_num + 1}.")

The smallest loss is 0.7491510596186821 at line number 280.


In [11]:
# Define paths and any environment variables first
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_l_tiktok6000_ucf101_{split_num}_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_large_patch16_224/checkpoint-279.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters (Adjust these as per your requirements)

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_large_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 4 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 50 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=4, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_l_tiktok6000_ucf101_1_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=50, eval=False, eval_data_path=None, finetune='/home/exouser/VideoMAEv2/work

In [5]:
# Define paths and any environment variables first
OUTPUT_DIR = 'work_dir/pretrain_videomae_large_patch16_224_epoch200'
DATA_PATH = 'train.csv'

import os
# --num_workers 24 
# Set environment variable
os.environ["OMP_NUM_THREADS"] = "1"

# Execute the python script with necessary parameters
!python -u run_mae_pretraining.py \
        --data_path {DATA_PATH} \
        --mask_type tube \
        --mask_ratio 0.9 \
        --decoder_mask_type run_cell \
        --decoder_mask_ratio 0.5 \
        --model pretrain_videomae_large_patch16_224 \
        --decoder_depth 4 \
        --batch_size 16 \
        --num_frames 16 \
        --sampling_rate 4 \
        --num_sample 2 \
        --num_workers 28 \
        --auto_resume \
        --opt adamw \
        --lr 1e-3 \
        --clip_grad 0.02 \
        --opt_betas 0.9 0.95 \
        --warmup_epochs 20 \
        --save_ckpt_freq 20 \
        --epochs 200 \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR}

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(auto_resume=True, batch_size=16, clip_grad=0.02, color_jitter=0.0, data_path='train.csv', data_root='', decoder_depth=4, decoder_mask_ratio=0.5, decoder_mask_type='run_cell', device='cuda', dist_on_itp=False, dist_url='env://', distributed=False, drop_path=0.0, epochs=200, finetune='', fname_tmpl='img_{:05}.jpg', imagenet_default_mean_and_std=True, input_size=224, local_rank=-1, log_dir='work_dir/pretrain_videomae_large_patch16_224_epoch200', lr=0.001, mask_ratio=0.9, mask_type='tube', min_lr=1e-05, model='pretrain_videomae_large_patch16_224', momentum=0.9, normlize_target=True, num_frames=16, num_sample=2, num_workers=28, opt='adamw', opt_betas=[0.9, 0.95], opt_eps=1e-08, output_